# Processing CSV files

In [19]:
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import data_processing as dp

pd.options.display.float_format = '{:.4f}'.format

IMU_list = ['BMI270', 'BMI055', 'ICM42688', 'MPU6000']

datasets = ['ATT', 'IMU']

# Adding fast sensor readings 
datasets += ['RGY', 'RAC']

df_dict = dp.load_suspend_data(datasets,imu=IMU_list[1])

df_transition = dp.compute_transition_df(source_df=df_dict['GT'], param='Ground_Truth')

print("[**] transition dataframe")
print(df_transition)


[**] transition dataframe
       timestamp  Ground_Truth  transition
1216     25.6519             0     -1.0000
8716     29.4021             1      1.0000
11216    30.6574             0     -1.0000
18716    34.4100             1      1.0000
21216    35.6600             0     -1.0000
28716    39.4101             1      1.0000
31216    40.6649             0     -1.0000
38716    44.4175             1      1.0000
41216    45.6675             0     -1.0000
48716    49.4175             1      1.0000
51216    50.6729             0     -1.0000
58716    54.4255             1      1.0000
61216    55.6755             0     -1.0000
68716    59.4255             1      1.0000
71216    60.6810             0     -1.0000
78716    64.4336             1      1.0000
81216    65.6836             0     -1.0000
88716    69.4335             1      1.0000
91216    70.6889             0     -1.0000


## Enriching Datasets

In [20]:
df=df_dict['GT']
param='Ground_Truth'
stats_params = {  
            'IMU': 
                ['GyrX', 'GyrY', 'GyrZ', 'AccX', 'AccY', 'AccZ'],
            'RAC':
                ['ACCx'],#'ACCy','ACCz'],
            'RGY':
                ['GYROx'],#'GYROy','GYROz'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw']
        }


# Add attack column into based on timestamps from the transition dataframe
for k in stats_params.keys():
    attack0 = df[param].iloc[0]
    attack = list()
    this_df = df_dict[k]
    tr0 = 0
    for tr in df_transition['timestamp'].values:
        data_size = len(this_df[(this_df['timestamp']>tr0) & (this_df['timestamp']<=tr)])
        # print('adding {} data points to {} points'.format(data_size, len(attack)))
        attack += [attack0]*data_size
        attack0 = df_transition['Ground_Truth'][df_transition['timestamp']==tr].values[0]
        tr0 = tr
    # Compute last segment
    data_size = len(this_df[this_df['timestamp']>tr])
    # print('adding {} data points to {} points'.format(data_size, len(attack)))
    attack += [attack0]*data_size
    this_df['attack'] = attack
    
    # Add 'update' column with the time diference between data points
    this_df['update'] = this_df['timestamp'].diff()

    df_dict[k] = this_df

update_dict = dict()
for ds in datasets[:-1]:
    df_update = pd.DataFrame()
    df_update['timestamp'] = df_dict[ds]['timestamp']
    df_update['update'] = df_dict[ds]['timestamp'].diff()
    update_dict[ds] = df_update
    

# Statistical Results

In [21]:

stat_dict = dict()
param_set = list()

for k,values in stats_params.items():
    for v in values+['update']:
        this_df = df_dict[k]
        # tr0 = 0
        # compute mean and std deviation for all variables in 'stats_params'
        atk_set = this_df['attack'].unique()
        for atk in atk_set:
            if 'update' in v:
                filtered_list = 1/this_df[v][this_df['attack']==atk]
            else:
                filtered_list = this_df[v][this_df['attack']==atk]

            mean_value = filtered_list.mean()
            std_value = filtered_list.std()

            # fill up the stat_dict dictionary by attack
            name_code = '{}.{}'.format(k, v)
            param_set.append(name_code)
            if atk in stat_dict:
                    stat_dict[atk][name_code] = {'mean': mean_value, 'std':std_value}
            else:
                stat_dict[atk] = {name_code:{'mean': mean_value, 'std':std_value}}

# convert stats into a dataframe
df_columns = ['Freq']
for i in list(set(param_set)):
    df_columns+= [i+'.mean', i+'.std']
stat_df = pd.DataFrame(columns=df_columns)
stat_df['Freq'] = atk_set
for freq in stat_dict:
    for param in stat_dict[freq]:
        stat_df.loc[stat_df['Freq']==freq,param+'.mean'] = stat_dict[freq][param]['mean']
        stat_df.loc[stat_df['Freq']==freq,param+'.std'] = stat_dict[freq][param]['std']

pd.options.display.float_format = '{:.4f}'.format
print(stat_df.loc[stat_df['Freq']!=0])
print(stat_df[['IMU.AccX.mean', 'IMU.AccX.std',
               'IMU.AccY.mean', 'IMU.AccY.std',
               'IMU.AccZ.mean', 'IMU.AccZ.std',
               'IMU.GyrX.mean', 'IMU.GyrX.std',
               'IMU.GyrY.mean', 'IMU.GyrY.std',
               'IMU.GyrZ.mean', 'IMU.GyrZ.std',]].loc[stat_df['Freq']!=0].to_latex())

   Freq RAC.ACCx.mean RAC.ACCx.std IMU.AccY.mean IMU.AccY.std IMU.GyrZ.mean  \
0     1       -0.3551       0.0620       -0.2340       0.0069        0.0012   

  IMU.GyrZ.std IMU.GyrY.mean IMU.GyrY.std RAC.update.mean  ...  \
0       0.0001       -0.0020       0.0002      17372.3326  ...   

  ATT.update.mean ATT.update.std IMU.AccZ.mean IMU.AccZ.std IMU.AccX.mean  \
0        407.4871        59.8814       -9.9745       0.0101       -0.4008   

  IMU.AccX.std IMU.GyrX.mean IMU.GyrX.std ATT.Roll.mean ATT.Roll.std  
0       0.0125       -0.0025       0.0003        0.7085       0.0055  

[1 rows x 31 columns]
\begin{tabular}{lllllllllllll}
\toprule
 & IMU.AccX.mean & IMU.AccX.std & IMU.AccY.mean & IMU.AccY.std & IMU.AccZ.mean & IMU.AccZ.std & IMU.GyrX.mean & IMU.GyrX.std & IMU.GyrY.mean & IMU.GyrY.std & IMU.GyrZ.mean & IMU.GyrZ.std \\
\midrule
0 & -0.400790 & 0.012518 & -0.233991 & 0.006904 & -9.974512 & 0.010130 & -0.002529 & 0.000262 & -0.001982 & 0.000208 & 0.001229 & 0.000131 \\
\bottom

## Plotting Suspend attack results

In [22]:
import plot_formatting as pfg

layout = go.Layout( autosize=True, margin={'l': 0, 'r': 0, 't': 20, 'b': 0})

fig = make_subplots(rows=4, cols=1,
                    shared_xaxes=True,
                    vertical_spacing = 0.02,
                    row_heights=[.25]*2 + [.25]*2)

colorset = px.colors.qualitative.Bold

# Plot data source
plot_params = {  
            'IMU': 
                ['GyrX', 'AccX'],
            'RAC':
                ['ACCx', 'update'],
            'RGY':
                ['GYROx', 'update'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw', 'update'],
        }


plot_labels = {
                'IMU': {'GyrX':'Gyro at controller',
                        'AccX':'Acc at controller'},
                'RAC':'Received Accel', 
               'RGY': 'Received Gyro',
               'ATT': 'EKF Estimation'}

x_range = [54, 55.5]

color_ix = 0
for k,values in plot_params.items():
    for v in values:
        row_num  = 1
        this_df = df_dict[k]
        this_df = this_df.loc[(this_df['timestamp']>x_range[0]) & (this_df['timestamp']<x_range[1])]
        if 'G' in v:
            row_num = 2
        tr0 = 0
        # Plotting attitude
        if 'ATT' in k and not ('update' in v):
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= v,
                    mode='lines',
                    legendgroup=k,
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=3,
                    legendgrouptitle_text='Attitude'),
                row=3,col=1)
        # Plotting update frequencies
        elif 'update' in v:
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=1/this_df[v],
                    name= plot_labels[k],
                    mode='lines',
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=5,
                    legendgroup='freq',
                    legendgrouptitle_text='Frequency'),
                row=4,col=1)
        else:
            # Plotting Accelerometer and Gyro

            if 'Gyr' in v or 'GYR' in v:
                group = 'GyroX'
            if 'Acc' in v:
                group = 'AccelX'
            try:
                fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                        name= plot_labels[k][v],#k+str('.')+v,
                        mode='lines',
                        line=dict(color=colorset[color_ix]),
                        showlegend=True,
                        legendgroup=group,
                        legendgrouptitle_text=group),
                    row=row_num,col=1)
            except:
                    fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                        name= plot_labels[k],
                        mode='lines',
                        line=dict(color=colorset[color_ix]),
                        showlegend=True,
                        legendgroup=group,
                        legendgrouptitle_text=group),
                        row=row_num,col=1)

        color_ix += 1


# Plot attacks
df = df_dict['GT']
df = df.loc[(df['timestamp']>x_range[0]) & (df['timestamp']<x_range[1])]


# inlcude attack transitions as vertical lines in the figure 
for v in df_transition['timestamp'][(df_transition['timestamp']>x_range[0]) & (df_transition['timestamp']<x_range[1])].values:
    fig.add_vline(x=v)

# beautify plots
fig = pfg.beautify_plot(fig)

subplot_titles=['value', 'data rate', 'freq'],
fig['layout'].update(layout)
#  Formating x-axis
fig['layout']['xaxis'].update(range=x_range)
fig['layout']['xaxis4'].update(title='Time [s]', mirror=True)

# Formating y-axis
fig['layout']['yaxis1'].update(title='Accel X [m/s/s]')
fig['layout']['yaxis2'].update(title='Gyro X [rad/s]', tickvals = [-0.01, 0.00, 0.01, 0.02, 0.03])
fig['layout']['yaxis4'].update(title='Frequency [Hz]', range=[100,3000])
fig['layout']['yaxis3'].update(title='Attitude [°]')

fig['layout']['legend'].update(orientation='h',
                                x=0.05,
                                y=0.45,
                                   )

fig.show()


In [23]:
fig.write_image('figs/BMI055Suspend_paper.pdf')

## Plotting Frequency attack results

In [24]:
import data_processing as dp

IMU_list = ['BMI270', 'BMI055', 'ICM42688', 'MPU6000']

datasets = ['ATT', 'IMU']
# Adding fast sensor readings 
datasets += ['RGY', 'RAC']

df_dict = dp.load_frequency_data(datasets,imu=IMU_list[1])

df_transition = dp.compute_transition_df(source_df=df_dict['AC'], param='Ground_Truth')
print("[**] transition dataframe")
print(df_transition)

[**] transition dataframe
        timestamp  Ground_Truth  transition
9754      39.4115        7.8125     -7.8125
19754     44.4170     1000.0000    992.1875
29754     49.4170      500.0000   -500.0000
39754     54.4225      250.0000   -250.0000
49754     59.4225      125.0000   -125.0000
59754     64.4285       62.5000    -62.5000
69754     69.4285       31.2500    -31.2500
79754     74.4350       15.6250    -15.6250
89754     79.4350        7.8125     -7.8125
99754     84.4415     1000.0000    992.1875
109754    89.4415      500.0000   -500.0000
119754    94.4475      250.0000   -250.0000
129754    99.4475      125.0000   -125.0000
139754   104.4540       62.5000    -62.5000
149754   109.4540       31.2500    -31.2500
159754   114.4610       15.6250    -15.6250
169754   119.4610        7.8125     -7.8125
179754   124.4665     1000.0000    992.1875
189754   129.4665      500.0000   -500.0000
199754   134.4715      250.0000   -250.0000
209754   139.4715      125.0000   -125.0000
219754

In [25]:
## Enriching Dataset

df=df_dict['AC']
param='Ground_Truth'
stats_params = {  
            'IMU': 
                ['GyrX', 'GyrY', 'GyrZ', 'AccX', 'AccY', 'AccZ'],
            'RAC':
                ['ACCx','ACCy','ACCz'],
            'RGY':
                ['GYROx','GYROy','GYROz'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw']
        }


# Add attack column into based on timestamps from the transition dataframe
for k in stats_params.keys():
    attack0 = df[param].iloc[0]
    attack = list()
    this_df = df_dict[k]
    tr0 = 0
    for tr in df_transition['timestamp'].values:
        data_size = len(this_df[(this_df['timestamp']>tr0) & (this_df['timestamp']<=tr)])
        # print('adding {} data points to {} points'.format(data_size, len(attack)))
        attack += [attack0]*data_size
        attack0 = df_transition['Ground_Truth'][df_transition['timestamp']==tr].values[0]
        tr0 = tr
    # Compute last segment
    data_size = len(this_df[this_df['timestamp']>tr])
    # print('adding {} data points to {} points'.format(data_size, len(attack)))
    attack += [attack0]*data_size
    this_df['attack'] = attack
    
    # Add 'update' column with the time diference between data points
    this_df['update'] = this_df['timestamp'].diff()

    df_dict[k] = this_df

update_dict = dict()
for ds in datasets[:-1]:
    df_update = pd.DataFrame()
    df_update['timestamp'] = df_dict[ds]['timestamp']
    df_update['update'] = df_dict[ds]['timestamp'].diff()
    update_dict[ds] = df_update



## Statistical Result

stat_dict = dict()
param_set = list()

for k,values in stats_params.items():
    for v in values+['update']:
        this_df = df_dict[k]
        # tr0 = 0
        # compute mean and std deviation for all variables in 'stats_params'
        atk_set = this_df['attack'].unique()
        for atk in atk_set:
            if 'update' in v:
                filtered_list = 1/this_df[v][this_df['attack']==atk]
            else:
                filtered_list = this_df[v][this_df['attack']==atk]

            mean_value = filtered_list.mean()
            std_value = filtered_list.std()

            # fill up the stat_dict dictionary by attack
            name_code = '{}.{}'.format(k, v)
            param_set.append(name_code)
            if atk in stat_dict:
                    stat_dict[atk][name_code] = {'mean': mean_value, 'std':std_value}
            else:
                stat_dict[atk] = {name_code:{'mean': mean_value, 'std':std_value}}

# convert stats into a dataframe
df_columns = ['Freq']
for i in list(set(param_set)):
    df_columns+= [i+'.mean', i+'.std']
stat_df = pd.DataFrame(columns=df_columns)
stat_df['Freq'] = atk_set
for freq in stat_dict:
    for param in stat_dict[freq]:
        stat_df.loc[stat_df['Freq']==freq,param+'.mean'] = stat_dict[freq][param]['mean']
        stat_df.loc[stat_df['Freq']==freq,param+'.std'] = stat_dict[freq][param]['std']


print(stat_df.loc[stat_df['Freq']!=0])
print(stat_df.to_latex())

       Freq RAC.update.mean RAC.update.std ATT.Yaw.mean ATT.Yaw.std  \
0   15.6250         31.9854         0.2611     349.0627      9.7088   
1    7.8125         16.1208         1.4614     347.3174      7.3316   
2 1000.0000       4165.8440     13464.7067     159.0739    170.6015   
3  500.0000       1127.4949      2563.3874     227.6194    161.3304   
4  250.0000        516.9089        52.1262     232.8618    161.6723   
5  125.0000        258.4730        77.3228     200.6589    169.8607   
6   62.5000        128.3170         7.2311      69.5193    139.5478   
7   31.2500         64.0058         0.8785     355.0475     14.2699   

  RGY.GYROz.mean RGY.GYROz.std RGY.GYROy.mean RGY.GYROy.std ATT.update.mean  \
0        -0.0462        1.8136        -0.0475        1.8138         33.2649   
1         0.0010        0.0011        -0.0003        0.0032         16.1213   
2         0.0002        0.0106         0.0007        0.0126        400.9214   
3        -0.0056        0.3071        -0.007

In [26]:
import plot_formatting as pfg

fig = make_subplots(rows=4, cols=1,
                    shared_xaxes=True,
                    vertical_spacing = 0.02,
                    row_heights=[.25]*2 + [.25]*2)

colorset = px.colors.qualitative.Vivid

# Plot data source
plot_params = {  
            'IMU': 
                ['GyrX', 'AccX', 'update'],
            'RAC':
                ['ACCx', 'update'],
            'RGY':
                ['GYROx', 'update'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw', 'update'],
        }

# Legend labels
plot_labels = {'RAC':'Accel', 
               'RGY': 'Gyro',
               'ATT': 'EKF Estimation',
               'IMU': 'IMU'}

x_range = [84,124]

color_ix = 0
for k,values in plot_params.items():
    for v in values:
        row_num  = 1
        this_df = df_dict[k][::1000]
        this_df = this_df.loc[(this_df['timestamp']>x_range[0]) & (this_df['timestamp']<x_range[1])]
        if 'G' in v:
            row_num = 2

        tr0 = 0
        if 'ATT' in k and not ('update' in v):
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= v,
                    mode='lines+markers',
                    legendgroup=k,
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=3,
                    legendgrouptitle_text='Attitude'),
                row=3,col=1)
        # PLotting update frequencies
        elif 'update' in v:
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=1/this_df[v],
                    name= plot_labels[k],
                    mode='lines+markers',
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=5,
                    legendgroup='freq',
                    legendgrouptitle_text='Frequency',
                    opacity=0.5),
                row=4,col=1)
        else:
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= v,
                    mode='lines+markers',
                    legendgroup=v,
                    line=dict(color=colorset[color_ix]),
                    showlegend=False),
                row=row_num,col=1)


        color_ix += 1

# Plot attacks
df = df.loc[(df['timestamp']>x_range[0]) & (df['timestamp']<x_range[1])]
# inlcude attack transitions as vertical lines in the figure 
for v in df_transition['timestamp'][(df_transition['timestamp']>x_range[0]) & (df_transition['timestamp']<x_range[1])].values:
    fig.add_vline(x=v)


# beautify plots
fig = pfg.beautify_plot(fig)

subplot_titles=['value', 'data rate', 'freq'],

#  Formating x-axis
fig['layout']['xaxis'].update(range=x_range)
fig['layout']['xaxis1'].update(side='top', mirror=True)
fig['layout']['xaxis2'].update(side='top', mirror=True)
fig['layout']['xaxis3'].update(mirror=True)
fig['layout']['xaxis4'].update(title='Time [s]', mirror=True)
# fig['layout'].update(yaxis_type="log", yaxis_range=[.0045,2])

# Formating y-axis
# fig['layout']['yaxis1'].update(range=[141.52,141.53], tickvals = [141.52, 141.53],)
fig['layout']['yaxis1'].update(title='Accelerometer X [m/s/s]')
# fig['layout']['yaxis2'].update(range=[0.45,0.55])
# fig['layout']['yaxis3'].update(range=[31.47,31.5], tickvals = [31.47,31.5],)
fig['layout']['yaxis2'].update(title='Gyro X [rad/s]')
# fig['layout']['yaxis4'].update(range=[-0.015,0.015])
fig['layout']['yaxis4'].update(title='Frequency [Hz]')
fig['layout']['yaxis3'].update(title='Attitude [°]')
fig['layout']['yaxis4'].update(range=[0,4], type='log')

fig['layout']['legend'].update(orientation='h',
                                x=0.65,
                                y=0.45,
                                   )

# fig.show()


layout.Legend({
    'borderwidth': 2, 'orientation': 'h', 'x': 0.65, 'y': 0.45
})

In [27]:
import plot_formatting as pfg
import plotly.graph_objects as go
layout = go.Layout( autosize=True, margin={'l': 0, 'r': 0, 't': 0, 'b': 0})
fig = go.Figure(layout=layout)
fig2 = go.Figure()

colorset = px.colors.qualitative.Vivid

# Plot data source
plot_params = {  
            #'IMU': 
            #    ['GyrX', 'AccX', 'update'],
            'RAC':
                ['ACCx', 'update'],
            'RGY':
                ['GYROx', 'update'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw', 'update'],
        }

# Legend labels
plot_labels = {'RAC':'Accel', 
               'RGY': 'Gyro',
               'ATT': 'EKF Estimation',
               'IMU': 'Processed IMU'}

x_range = [85,124]

color_ix = 0
for k,values in plot_params.items():
    for v in values:
        row_num  = 1
        this_df = df_dict[k]
        this_df = this_df.loc[(this_df['timestamp']>x_range[0]) & (this_df['timestamp']<x_range[1])]
        if 'G' in v:
            row_num = 2

        tr0 = 0
        if 'update' in v:
            print(this_df)
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=1/this_df[v],
                    name= plot_labels[k],
                    mode='lines',
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    # legendrank=5,
                    # legendgroup='freq',
                    # legendgrouptitle_text='Frequency',
                    opacity=0.8))
            fig2.add_violin(x=this_df['attack'], y=1/this_df[v], name=plot_labels[k])
            color_ix += 1

# Plot attacks
df = df.loc[(df['timestamp']>x_range[0]) & (df['timestamp']<x_range[1])]
# inlcude attack transitions as vertical lines in the figure 
for v in df_transition['timestamp'][(df_transition['timestamp']>x_range[0]) & (df_transition['timestamp']<x_range[1])].values:
    fig.add_vline(x=v)

fig = pfg.beautify_plot(fig)


fig['layout'].update(width=800, height=400, font_size = 25)
fig['layout']['yaxis'].update(range=[1,4], type='log')

fig['layout']['xaxis'].update(title='Time [s]', mirror=True, range=x_range)
fig['layout']['yaxis'].update(title='Frequency [Hz]')

fig['layout']['legend'].update(orientation='h',
                                x=0.3,
                                y=1,
                                   )

# beautify plots
fig.show()

fig2 = pfg.beautify_plot(fig2)


fig2['layout'].update(width=1200, height=400,font_size = 25)
fig2['layout']['yaxis'].update(range=[1,4], type='log')

fig2['layout']['xaxis'].update(title='Freq set [Hz]')
fig2['layout']['yaxis'].update(title='Frequency [Hz]', type='log')

fig2['layout']['legend'].update(orientation='h',
                                x=0.05,
                                y=1.2,
                                   )
fig2.show()

       timestamp     TimeUS    ACCx   TimeUS.1  ACCx.1    ACCy    ACCz  \
21782    85.0000   85000014 -0.6893   85000014 -0.6893  0.0000 -9.9567   
21783    85.0005   85000536 -0.7659   85000536 -0.7659  0.0000 -9.7269   
21784    85.0010   85001032 -0.7659   85001032 -0.7659  0.0766 -9.8801   
21785    85.0015   85001520 -0.6893   85001520 -0.6893  0.0000 -9.8801   
21786    85.0020   85002019 -0.7659   85002019 -0.7659 -0.0766 -9.8801   
...          ...        ...     ...        ...     ...     ...     ...   
41035   123.7360  123735993 -0.6893  123735993 -0.6893 -0.0766 -9.8801   
41036   123.7985  123798491 -0.6893  123798491 -0.6893 -0.0766 -9.8801   
41037   123.8615  123861488 -0.6893  123861488 -0.6893 -0.0766 -9.8801   
41038   123.9240  123923992 -0.6893  123923992 -0.6893 -0.0766 -9.8801   
41039   123.9865  123986490 -0.6893  123986490 -0.6893 -0.0766 -9.8801   

         attack  update  
21782 1000.0000  0.0005  
21783 1000.0000  0.0005  
21784 1000.0000  0.0005  
21785 1

In [28]:
fig.write_image('figs/BMI055Frequency_paper.pdf')